## Limpieza del set de datos de Properatti

In [1]:
import pandas as pd
import numpy as np
import re

Vamos a tomar la data

In [21]:
df = pd.read_csv("properatti.csv")

In [37]:
del df['titulo_lower']
del df['descrip_lower']

Vamos a samplear la data, para empezar la exploración y entender los datos:

In [38]:
df.head()

Unnamed: 0 operation property_type place_name  \
0           0      sell            PH  Mataderos   
1           1      sell     apartment   La Plata   
2           2      sell     apartment  Mataderos   
3           3      sell            PH    Liniers   
4           4      sell     apartment     Centro   

                             place_with_parent_names country_name  \
0              |Argentina|Capital Federal|Mataderos|    Argentina   
1        |Argentina|Bs.As. G.B.A. Zona Sur|La Plata|    Argentina   
2              |Argentina|Capital Federal|Mataderos|    Argentina   
3                |Argentina|Capital Federal|Liniers|    Argentina   
4  |Argentina|Buenos Aires Costa Atlántica|Mar de...    Argentina   

                     state_name  geonames_id                  lat-lon  \
0               Capital Federal    3430787.0  -34.6618237,-58.5088387   
1        Bs.As. G.B.A. Zona Sur    3432039.0  -34.9038831,-57.9643295   
2               Capital Federal    3430787.0  -34.6522615,-58.5229825   
3               Capital Federal    3431333.0  -34.6477969,-58.5164244   
4  Buenos Aires Costa Atlántica    3435548.0  -38.0026256,-57.5494468   

         lat                        ...                          \
0 -34.661824                        ...                           
1 -34.903883                        ...                           
2 -34.652262                        ...                           
3 -34.647797                        ...                           
4 -38.002626                        ...                           

   surface_covered_in_m2  price_usd_per_m2 price_per_m2  floor  rooms  \
0                   40.0       1127.272727  1550.000000    NaN    NaN   
1                    NaN               NaN          NaN    NaN    NaN   
2                   55.0       1309.090909  1309.090909    NaN    NaN   
3                    NaN               NaN          NaN    NaN    NaN   
4                   35.0       1828.571429  1828.571429    NaN    NaN   

   expenses                                      properati_url  \
0       NaN  http://www.properati.com.ar/15bo8_venta_ph_mat...   
1       NaN  http://www.properati.com.ar/15bob_venta_depart...   
2       NaN  http://www.properati.com.ar/15bod_venta_depart...   
3       NaN  http://www.properati.com.ar/15boh_venta_ph_lin...   
4       NaN  http://www.properati.com.ar/15bok_venta_depart...   

                                         description  \
0  2 ambientes tipo casa planta baja por pasillo,...   
1  venta de departamento en décimo piso al frente...   
2  2 ambientes 3er piso lateral living comedor am...   
3  ph 3 ambientes con patio. hay 3 deptos en lote...   
4  departamento con fantástica iluminación natura...   

                                               title  \
0                 2 amb tipo casa sin expensas en pb   
1  venta depto 2 dorm. a estrenar 7 e/ 36 y 37   ...   
2           2 amb 3er piso con ascensor apto credito   
3                       ph 3 amb. cfte. reciclado      
4  depto 2 amb al contrafrente zona centro/plaza ...   

                                     image_thumbnail  
0  https://thumbs4.properati.com/8/BluUYiHJLhgIIK...  
1  https://thumbs4.properati.com/7/ikpVBu2ztHA7jv...  
2  https://thumbs4.properati.com/5/SXKr34F_IwG3W_...  
3  https://thumbs4.properati.com/3/DgIfX-85Mog5SP...  
4  https://thumbs4.properati.com/5/xrRqlNcSI_vs-f...  

[5 rows x 26 columns]

Las columnas que vamos a utilizar en el analisis las pasamos a minuscula para simplificar el parseado.

In [33]:
df['title'] = df['title'].str.lower()
df['description'] = df['description'].str.lower()

Vamos a entender los campos de 'operation':

In [7]:
set(df['operation'])

{'sell'}

Vamos a entender los campos de 'property_type':

In [8]:
set(df['property_type'])

{'PH', 'apartment', 'house', 'store'}

Vamos a entender los campos de 'place_name':

In [31]:
random.sample(set(df['place_name']),20)

NameError: name 'random' is not defined

Vamos a ver la info del Data Frame

In [10]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 121220 entries, 0 to 121219
Data columns (total 26 columns):
Unnamed: 0                    121220 non-null int64
operation                     121220 non-null object
property_type                 121220 non-null object
place_name                    121197 non-null object
place_with_parent_names       121220 non-null object
country_name                  121220 non-null object
state_name                    121220 non-null object
geonames_id                   102503 non-null float64
lat-lon                       69670 non-null object
lat                           69670 non-null float64
lon                           69670 non-null float64
price                         100810 non-null float64
currency                      100809 non-null object
price_aprox_local_currency    100810 non-null float64
price_aprox_usd               100810 non-null float64
surface_total_in_m2           81892 non-null float64
surface_covered_in_m2         101313 no

El campo rooms tiene 47390 entradas válidas. Vamos a ver si podemos completar

# Vamos a completar la información faltante en base a un diccionario

### Creo el diccionario del parser
Cada nueva fila debe tener formato: ['regEx para buscar', 'regEx para extraer números contenidos dentro del resultado de la regEx de búsqueda', 'columna donde buscar', 'columna donde guardar el dato faltante', 'tipo del dato a extraer']

In [22]:
col_names =  ['lookup_regex', 'extract_regex', 'column_to_lookup','column_to_complete','value_type','value_offset','extra_condition']
diccionario  = pd.DataFrame(columns = col_names)
#Nueva fila a agregar al diccionario. Va a tomar números entre 0 y 99 seguidos de entre 1 y 3 espacios, más amb o AMB o AMB.
#Va a revisar la columna 'title' y va a escribir los valores que encuentre en la columna 'rooms'
#diccionario.loc[len(diccionario)] = ['\d{1,2} {1,3}amb|\d{1,2} {1,3}AMB*|\d{1,2} {1,3}Amb*', '\d{1,2}', 'title', 'rooms', 'float',0, {'data_column' : 'country_name', 'value' : 'Argentina', 'condition_func': (lambda x,y: x == y)}]
#Nueva fila a agregar al diccionario. Va a tomar números entre 0 y 99 seguidos de entre 1 y 3 espacios, más amb o AMB o AMB.
#Va a revisar la columna 'description' y va a escribir los valores que encuentre en la columna 'rooms'
#diccionario.loc[len(diccionario)] = ['\d{1,2} {1,3}amb|\d{1,2} {1,3}AMB*|\d{1,2} {1,3}Amb*', '\d{1,2}', 'description', 'rooms', 'float',0, {'data_column' : 'country_name', 'value' : 'Argentina', 'condition_func': (lambda x,y: x == y)}] #Nueva fila a agregar
#diccionario.loc[len(diccionario)] = ['/d abc', '/d', 'description', 'metros2', 'float',0,{'data_column' : 'country_name', 'value' : 'Argentina', 'condition_func': (lambda x,y: x == y)}] #Nueva fila a agregar
#diccionario.loc[len(diccionario)] = ['monoamb|Monoamb|MONOAMB', '', 'description', 'rooms', 'float',1, {'data_column' : 'country_name', 'value' : 'Argentina', 'condition_func': (lambda x,y: x == y)}]
#diccionario.loc[len(diccionario)] = ['monoamb|Monoamb|MONOAMB', '', 'title', 'rooms', 'float',1, {'data_column' : 'country_name', 'value' : 'Argentina', 'condition_func': (lambda x,y: x == y)}]
#diccionario.loc[len(diccionario)] = ['quinto|QUINTO|Quinto', '', 'title', 'floor', 'float',5, {'data_column' : 'country_name', 'value' : 'Argentina', 'condition_func': (lambda x,y: x == y)}]
#diccionario.loc[len(diccionario)] = ['quinto|QUINTO|Quinto', '', 'description', 'floor', 'float',5, {'data_column' : 'country_name', 'value' : 'Argentina', 'condition_func': (lambda x,y: x == y)}]
diccionario.loc[len(diccionario)] = ['Sup {0,3}\d{1,3} {0,3}Mts|SUP {0,3}\d{1,3} {0,3}MTS|sup {0,3}\d{1,3} {0,3}mts', '\d{1,3}', 'title', 'surface_covered_in_m2', 'float',0, {'data_column' : 'country_name', 'value' : 'Argentina', 'condition_func': (lambda x,y: x == y)}]
diccionario.loc[len(diccionario)] = ['Sup {0,3}\d{1,3} {0,3}Mts|SUP {0,3}\d{1,3} {0,3}MTS|sup {0,3}\d{1,3} {0,3}mts', '\d{1,3}', 'description', 'surface_covered_in_m2', 'float',0, {'data_column' : 'country_name', 'value' : 'Argentina', 'condition_func': (lambda x,y: x == y)}]
diccionario.loc[len(diccionario)] = ['\d{1,3} {0,3}MTS2|\d{1,3} {0,3}Mts2 |\d{1,3} {0,3}mts2', '\d{1,3}', 'title', 'surface_covered_in_m2', 'float',0, {'data_column' : 'country_name', 'value' : 'Argentina', 'condition_func': (lambda x,y: x == y)}]
diccionario.loc[len(diccionario)] = ['\d{1,3} {0,3}MTS2|\d{1,3} {0,3}Mts2 |\d{1,3} {0,3}mts2', '\d{1,3}', 'description', 'surface_covered_in_m2', 'float',0, {'data_column' : 'country_name', 'value' : 'Argentina', 'condition_func': (lambda x,y: x == y)}]
diccionario.loc[len(diccionario)] = ['\d{1,3} {0,3}Ms|\d{1,3} {0,3}MS |\d{1,3} {0,3}ms', '\d{1,3}', 'title', 'surface_covered_in_m2', 'float',0, {'data_column' : 'country_name', 'value' : 'Argentina', 'condition_func': (lambda x,y: x == y)}]
diccionario.loc[len(diccionario)] = ['\d{1,3} {0,3}Ms|\d{1,3} {0,3}MS |\d{1,3} {0,3}ms', '\d{1,3}', 'description', 'surface_covered_in_m2', 'float',0, {'data_column' : 'country_name', 'value' : 'Argentina', 'condition_func': (lambda x,y: x == y)}]
diccionario.loc[len(diccionario)] = ['\d{1,3} {0,3}M|\d{1,3} {0,3}m', '\d{1,3}', 'title', 'surface_covered_in_m2', 'float',0, {'data_column' : 'country_name', 'value' : 'Argentina', 'condition_func': (lambda x,y: x == y)}]
diccionario.loc[len(diccionario)] = ['\d{1,3} {0,3}M|\d{1,3} {0,3}m', '\d{1,3}', 'description', 'surface_covered_in_m2', 'float',0, {'data_column' : 'country_name', 'value' : 'Argentina', 'condition_func': (lambda x,y: x == y)}]


Veo el diccionario:

In [7]:
diccionario

lookup_regex extract_regex  \
0                               quinto|QUINTO|Quinto                 
1                               quinto|QUINTO|Quinto                 
2  \d{1,3} {0,3}Mts|\d{1,3} {0,3}MTS|\d{1,3} {0,3...       \d{1,3}   
3  \d{1,3} {0,3}Mts|\d{1,3} {0,3}MTS|\d{1,3} {0,3...       \d{1,3}   
4  \d{1,3} {0,3}MTS2|\d{1,3} {0,3}Mts2 |\d{1,3} {...       \d{1,3}   
5  \d{1,3} {0,3}MTS2|\d{1,3} {0,3}Mts2 |\d{1,3} {...       \d{1,3}   
6   \d{1,3} {0,3}Ms|\d{1,3} {0,3}MS |\d{1,3} {0,3}ms       \d{1,3}   
7   \d{1,3} {0,3}Ms|\d{1,3} {0,3}MS |\d{1,3} {0,3}ms       \d{1,3}   
8                      \d{1,3} {0,3}M|\d{1,3} {0,3}m       \d{1,3}   
9                      \d{1,3} {0,3}M|\d{1,3} {0,3}m       \d{1,3}   

  column_to_lookup     column_to_complete value_type value_offset  \
0            title                  floor      float            5   
1      description                  floor      float            5   
2            title  surface_covered_in_m2      float            0   
3      description  surface_covered_in_m2      float            0   
4            title  surface_covered_in_m2      float            0   
5      description  surface_covered_in_m2      float            0   
6            title  surface_covered_in_m2      float            0   
7      description  surface_covered_in_m2      float            0   
8            title  surface_covered_in_m2      float            0   
9      description  surface_covered_in_m2      float            0   

                                     extra_condition  
0  {'data_column': 'country_name', 'value': 'Arge...  
1  {'data_column': 'country_name', 'value': 'Arge...  
2  {'data_column': 'country_name', 'value': 'Arge...  
3  {'data_column': 'country_name', 'value': 'Arge...  
4  {'data_column': 'country_name', 'value': 'Arge...  
5  {'data_column': 'country_name', 'value': 'Arge...  
6  {'data_column': 'country_name', 'value': 'Arge...  
7  {'data_column': 'country_name', 'value': 'Arge...  
8  {'data_column': 'country_name', 'value': 'Arge...  
9  {'data_column': 'country_name', 'value': 'Arge...

Defino la función que procesa el dataframe iterando en base al diccionaro:

In [23]:
def df_parser(data,parse_dictionary):
    for pattern_row_index, pattern in parse_dictionary.iterrows():
        #print ("Looking for regular expression: '" + pattern["lookup_re"] + "' in column: '" + pattern["column_to_lookup"] + "', extracting number with regEx: '" + pattern["extract_re"]+"' and assigning value to column: '" + pattern["column_to_complete"] + "'")
        #print(pattern['extra_condition'])
        for data_row_index, row in data[ (data[pattern["column_to_complete"]].isnull() == True) &
                                         (pattern['extra_condition']['condition_func'] (data[pattern['extra_condition']['data_column']],pattern['extra_condition']['value']) == True) ].iterrows():
                                         #(1==1) ].iterrows():
        #for data_row_index, row in data.iterrows():
            #print(data.loc[data_row_index,pattern["column_to_complete"]])
            if type(data.loc[data_row_index,pattern["column_to_lookup"]]) is str and data.loc[data_row_index,pattern["column_to_lookup"]] != '':
                #print('Missing data here ...')
                matches = re.search(pattern["lookup_regex"], data.loc[data_row_index,pattern["column_to_lookup"]])
                if matches:
                    print('Regx Encontro: ')
                    print(matches.group(0)) #Imprime el valor encontrado dentro del campo que se está interpretando
                    print('En: ')
                    print(data.loc[data_row_index,pattern["column_to_lookup"]]) #Imprime el valor encontrado dentro del campo que se está interpretando
                    print('Va a sobrescribir: ')
                    print(data.loc[data_row_index,pattern["column_to_complete"]]) #Imprime el valor encontrado del campo que se está intentando llenar
                    print('Va a convertir: ')
                    print(re.search(pattern["extract_regex"], matches.group(0)).group(0)) #Imprime el string que va a ser extraído para convertir a número
                    if (pattern["value_type"] == 'float') and (pattern["extract_regex"] != ''):
                        number = float( re.search(pattern["extract_regex"], matches.group(0)).group(0) ) + pattern["value_offset"]
                    elif (pattern["value_type"] == 'int') and (pattern["extract_regex"] != ''):
                        number = int( re.search(pattern["extract_regex"], matches.group(0)).group(0) ) + pattern["value_offset"]
                    elif pattern["value_type"] == 'float':
                        number = float(pattern["value_offset"])
                    else:
                        number = int(pattern["value_offset"])
                    data.loc[data_row_index,pattern["column_to_complete"]] = number
                    print('Escribio: ')
                    #print(number)
                    print(data.loc[data_row_index,pattern["column_to_complete"]])
    return

### Corro la función para parsear la información

In [24]:
df_parser(df,diccionario)

Regx Encontro: 
900 mts2
En: 
Casa con lote de 900 mts2  céntrica en Avellaneda
Va a sobrescribir: 
nan
Va a convertir: 
900
Escribio: 
900.0
Regx Encontro: 
105 mts2
En: 
VENTA DUPLEX 2 dormitorios 105 mts2 B° ELEMENTOS N
Va a sobrescribir: 
nan
Va a convertir: 
105
Escribio: 
105.0
Regx Encontro: 
120 mts2
En: 
VENTA CASA PLANTA BAJA 120 mts2 Barrio ELEMENTOS
Va a sobrescribir: 
nan
Va a convertir: 
120
Escribio: 
120.0
Regx Encontro: 
250 mts2
En: 
Hermosa Casa en Arguello de 3 dorm 1250 mts2 de Terreno  Cordoba
Va a sobrescribir: 
nan
Va a convertir: 
250
Escribio: 
250.0
Regx Encontro: 
32 MTS2
En: 
DEPTOS MONO AMBIENTES 32 MTS2 A ESTRENAR!!! APTO CREDITO
Va a sobrescribir: 
nan
Va a convertir: 
32
Escribio: 
32.0
Regx Encontro: 
36mts2
En: 
Espectacular dpto.1 amb.a estrenar, c/fte, con balcón corrido 36mts2.
Va a sobrescribir: 
nan
Va a convertir: 
36
Escribio: 
36.0
Regx Encontro: 
41mts2
En: 
Espectacular dpto.2 amb., frente, balcón corrido, 41mts2 con patio
Va a sobrescribir:

Escribio: 
390.0
Regx Encontro: 
335mts2
En: 
TUZAINGO NTE CHALET DE 3 AMBIENTES, LOTE DE 335mts2, aprx. ( a refaccionar), u$s87.000. CONSULTE!! .Publicado por TORTOLINI PROPIEDADES a traves INMOMAP
Va a sobrescribir: 
nan
Va a convertir: 
335
Escribio: 
335.0
Regx Encontro: 
500 mts2
En: 
CHALET EN ITUZ NTE: BUENA ZONA.3 AMB, LOTE APROX 500 mts2, JARDIN, LIVING, COCINA COMEDOR DIARIO, 2 DORMITORIOS, 2 BAOS, E/ D AUTO. CONSULTE!! .Publicado por TORTOLINI PROPIEDADES a traves INMOMAP
Va a sobrescribir: 
nan
Va a convertir: 
500
Escribio: 
500.0
Regx Encontro: 
475 mts2
En: 
Lote en excelente zona de Vicente Lopez. Predominio de desarrollos inmobiliarios importantes de Oficinas y Viviendas.Se ubica a una cuadra de la Av. General Paz . Frente al supermercado Carrefour/Sodimac Dimensiones Frente sobre Av. del Libertador 12,5 mtsDimensiones Contra frente: 9.75 mtsLaterales 44 mts. Superficie Total: 475 mts2 aprox. ZONIFICACION T3L FOS: 0,6 FOT: 2,65 + premiosEl FOT del terreno con premios e

Escribio: 
550.0
Regx Encontro: 
4mts2
En: 
Corredor Responsable: Fabiana Di Girolamo - CDCPDJLP 7033Contacto: Andrés Alí - MLS ID # 420346 e/45 y 46 Monoambiente en 1er piso al frente de 36,4mts2 con balcón, orientación surdeste, baño completo, cocina equipada con cocina Orbis de 4 hornallas, calefon TB, muebles sobre y bajo mesada. Incluye estufa Orbis tiro balanceado; el edificio cuenta con terraza - laundry donde tambien encontramos las parrillas de uso común.-  Posee pisos de porcelanato, aberturas en línea Módena A30, DVH (doble vidrio hermético), Pre-instalación para aire acondicionado en dormitorio y living. Opción cochera (No incluida en el costo). Entrega aproximada Fin Octubre  2017
Va a sobrescribir: 
nan
Va a convertir: 
4
Escribio: 
4.0
Regx Encontro: 
44 mts2
En: 
Corredor Responsable: HORACIO RAUL PEREYRA - CDCPDJLP 7186Contacto: Damián Domínguez - MLS ID # 42071 entre 39 y 40. Monoambiente de 44 mts2 ubicado en piso 7° al frente. Posee 36 mts2 cubiertos y 8 mts2 de bal

Escribio: 
220.0
Regx Encontro: 
98 MTS2
En: 
CASA TRES AMBIENTES A LA VENTA EN SAN MIGUELVICENTE LOPEZ 3397, CALLAO Y RIVADAVIACASA TRES AMBIENTES SOBRE UN LOTE DE 8.66 X 34.64 MTS (TOTAL: 299.98 MTS2) CON LIVING COMEDOR, COCINA TIPO PASILLO CHICA CON AMOBLAMIENTO DE BAJO MESADA, BAÑO COMPLETO CON DUCHA, DOS DORMITORIOS, QUINCHO CON PARRILLA AL FRENTE, FONDO CHICO CON LAVADERO Y ESPACIO GUARDA ÚTILES. SERVICIOS: LUZ, GAS ENVASADO, AGUA POR BOMBEADOR.VALOR U$S 70.000.-CON POSIBILIDAD DE FINANCIACIÓN. -  - FEDERICO NEGRO ESTUDIO INMOBILIARIO
Va a sobrescribir: 
nan
Va a convertir: 
98
Escribio: 
98.0
Regx Encontro: 
40 mts2
En: 
Corredor Responsable: Pablo Castañeda - C.U.C.I.S. Mat. Nº208Contacto: Omar Fernández - MLS ID # 251121-58Casa estilo moderna, en cielos del valle, 40 mts2 aprox un terreno de 250 mts2 a estrenar, se entregaría a fines de julio. proyecto IKBA. Corredor Responsable: Pablo Castañeda C.U.C.I.S. Mat. Nº208  En cumplimiento de la Ley Provincial 7629, Ley Nacional 25.

Escribio: 
35.0
Regx Encontro: 
30 mts2
En: 
Contacto de consultas: Laura . Celular:  0-9002Luminoso departamento de 2 ambientes de 30 mts2. Ubicado en Martin Pescador entre Shaw y Valle Fertil ( a 6 cuadras del centro y 8 de la playa). Ideal para 1 persona o matrimonio. No cuenta con cochera propia pero el edificio cuenta con cocheras de cortesia en la entrada.
Va a sobrescribir: 
nan
Va a convertir: 
30
Escribio: 
30.0
Regx Encontro: 
400 mts2
En: 
Corredor Responsable: Pablo Castañeda - C.U.C.I.S. Mat. Nº208Contacto: Alberto M. Nanterne  Layun - MLS ID # 251084-122Propiedad ubicada en el B° Villa Lavalle emplazada en un terreno de 1400 mts2 con una construcción aproximada de 120 mts2 distribuidos de la siguiente manera: hall de ingreso, cocina (sin artefactos), 1 baño (sin sanitarios) living, 2 habitaciones,  una sala de estar y escalera con proyección de  terraza. Posee Escritura   Corredor Responsable: Pablo Castañeda C.U.C.I.S. Mat. Nº208  En cumplimiento de la Ley Provincial 762

...

Escribio: 
100.0
Regx Encontro: 
85 m
En: 
Amplio Departamento de 3 dormitorios en complejo cerrado, con cochera, construccion del año 1976, reciclado en 2014, con excelente ubicacion en Bº Bajo Palermo.Ubicado en 1er piso (sin ascensor), cuenta con amplio living comedor, gran pasillo distribuidor a los 3 dormitorios (esto tambien amplios con comodos placares), un baño completo. Cocina mediana con lavadero incluido, tambien reciclada con muy buen gusto.Cochera en el complejo, semi cubierta.Con escritura, apto crédito bancario.Sup propia del depto 85 m² mas cochera. 
Va a sobrescribir: 
nan
Va a convertir: 
85
Escribio: 
85.0
Regx Encontro: 
100m
En: 
En la intersección de la calle Rosario de Santa Fe con Paraná, a apenas 100m del centro Cívico del Bicentenario y a 200m de Bv. Chacabuco, se emplaza este imponente Edificio residencial de alta categoría con incorporación de 42 viviendas de uno y dos dormitorios. Cuenta con espacios comunes (piscina descubierta con solárium y asadores con 

Va a convertir: 
004
Escribio: 
4.0
Regx Encontro: 
7M
En: 
 OPORTUNIDAD APTO CREDITO. NO PERDER!!! AMPLIO Departamento  DOS  dormitoriosDos bañosCALEFACCION CENTRALCocina Separada 7Mo. Piso con BalcónUbicación privilegiada ZONA PLAZA ALTA CORDOBA Abelardo CalleAbogado – Negocios InmobiliariosCPI 4492Cel. +54 351 15 7063066 *El precio indicado es de referencia, sujeto a modificaciones sin previo aviso.*Los datos consignados en esta web pueden contener errores y son no contractuales; verifique los mismos con nuestros asesores. 
Va a sobrescribir: 
nan
Va a convertir: 
7
Escribio: 
7.0
Regx Encontro: 
53 m
En: 
Muy buen departamento, de ambientes amplios. Ubicado sobre la Av. Gral Paz al 600. Muy próximo al microcentro y zona de comercios. Al contrafrente luminoso con vista despejada.53 m2 propios.Living comedor, cocina separada, con muebles sobre y bajo mesada, 2 dormitorios, uno con placard con interiores y placares con alzada en pasillo de distribución. Baño completo. Oportunidad inve

Escribio: 
50.0
Regx Encontro: 
161m
En: 
Hermosa casa a estrenar de 2 dormitorios en #VENTA - Las Breñas - Terreno de 12.50 x 21.25 - Construidos: 161m2. Galería, baño, cocina living comedor, garage p/2autos y patio. #IDEAL para invertir en tu primer hogar - #Info: 0362 - 4581100
Va a sobrescribir: 
nan
Va a convertir: 
161
Escribio: 
161.0
Regx Encontro: 
300 M
En: 
CASA QUINTA DE 3 HABITACIONES, 2 PLANTAS, PARQUE, PILETA.PA: 3 HABITACIONES, 2 BAÑOS, BALCÓN.PB: COCINA-COMEDOR DIARIO, COMEDOR Y LIVING, 1 BAÑO.GARAGE PARA 2 AUTOS, PARRILLA, PILETA, PARQUE.PROPIEDAD SOBRE ASFALTO Y A 300 MTS DE RUTA Nº 2, EN EXCELENTE ESTADO Y UBICACIÓN.IDEAL VIVIENDA PERMANENTE O CASA DE FIN DE SEMANA . LISTA PARA ESCRITURAR.
Va a sobrescribir: 
nan
Va a convertir: 
300
Escribio: 
300.0
Regx Encontro: 
10m
En: 
Edificio de 10 pisos, 35 unidades en total.Del 1ro al 8vo piso 4 unidades por piso y en el 9no piso 3 unidades, en el 10mo piso se encuentra el SUM.Cuenta con 21 cocheras en PB y Subsuelo con po

Escribio: 
6.0
Regx Encontro: 
000 m
En: 
Departamentos de ALTO NIVEL , ubicado en el exclusivo Barrio Las Rosas, entre las calles Luis Galeano, Nazaret, y Costanera Norte. Dpto de 1 y 2 dormitorios , a estrenar , cocina equipada, living comedor , baño y antebaño,  calefacción en todos los ambientes, excelente iluminación y ventilación natural. El complejo posee 1000 m2 destinados a Amenities y Servicios; CLUB HOUSE  PISCINA OUTDOOR CON SOLÁRIUM, MICROCINE, WI-FI ZONE, SALONES DE USOS MÚLTIPLES, MODULABLES CON ASADORES, INDOOR GYM & FITNESS CENTER COCHERA OPCIONAL. Tel:564Cel:72841 Envía un whatsapp al 3517672841 con la palabra "INDICE 254" y te enviaremos mas información.Indice Inmobiliario Ofrecé o encontrá tu propiedad 72841
Va a sobrescribir: 
nan
Va a convertir: 
000
Escribio: 
0.0
Regx Encontro: 
65 m
En: 
OLSEN Propiedades te presenta esta alternativa de departamento.EXCELENTE DEPARTAMENTO EN ALTA CORDOBA - Calle Antonio del Viso 694 esquina Rivadavia - 2 dormitorios con placard

Escribio: 
24.0
Regx Encontro: 
24 m
En: 
CODIGO: 2400-IND08 ubicado en: Independencia -  Publicado por: BDF PROPIEDADES. El precio es de ARS 2008160 null. EDIFICIO: “GALA XVIII”  INDEPENDENCIA 5077 ENTRE LAVALLE Y GENERAL PAZ  CENTRO DE VILLA BALLESTER   Departamentos en Construccion: En cuotas y en pesos  Planos aprobados  Fecha de Inicio de Obra: Marzo 2016  Fecha de entrega estimada: 24 meses   Características de Edificio  •	Cantidad de Pisos:	8	Cantidad de Unidades:	45	 Unidades: “A” “B” “C” Al Frente  Unidades: “D” “E” “F”	Contra frente  •	Cantidad de Cocheras: 31 (cubiertas y descubiertas)  •	Ascensores de última generación con puerta automática y cabina de acero  •	Escalera de Servicio con escalones de hormigón armado con terminaciones en cemento alisado y barandas metálicas  •	Amplio Hall de Entrada con detalles de categoría  •	Portón de acceso a cocheras automatizado  •	Rampas de acceso para discapacitados  •	Agua caliente por Sistema Central   Características de las Unidades

In [25]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 121220 entries, 0 to 121219
Data columns (total 26 columns):
Unnamed: 0                    121220 non-null int64
operation                     121220 non-null object
property_type                 121220 non-null object
place_name                    121197 non-null object
place_with_parent_names       121220 non-null object
country_name                  121220 non-null object
state_name                    121220 non-null object
geonames_id                   102503 non-null float64
lat-lon                       69670 non-null object
lat                           69670 non-null float64
lon                           69670 non-null float64
price                         100810 non-null float64
currency                      100809 non-null object
price_aprox_local_currency    100810 non-null float64
price_aprox_usd               100810 non-null float64
surface_total_in_m2           81892 non-null float64
surface_covered_in_m2         108686 no

El campo rooms antes tenía 47390 entradas válidas. Ahora vemos que tiene 69080 entradas válidas

In [16]:
df.head(30)

Unnamed: 0 operation property_type           place_name  \
0            0      sell            PH            Mataderos   
1            1      sell     apartment             La Plata   
2            2      sell     apartment            Mataderos   
3            3      sell            PH              Liniers   
4            4      sell     apartment               Centro   
5            5      sell         house         Gualeguaychú   
6            6      sell            PH                Munro   
7            7      sell     apartment             Belgrano   
8            8      sell     apartment             Belgrano   
9            9      sell         house              Rosario   
10          10      sell         house              Córdoba   
11          11      sell         house           San Miguel   
12          12      sell     apartment             Martínez   
13          13      sell     apartment         Palermo Soho   
14          14      sell     apartment         Palermo Soho   
15          15      sell         house          Bella Vista   
16          16      sell            PH            Mataderos   
17          17      sell     apartment       Barrio El Golf   
18          18      sell         house                Tigre   
19          19      sell     apartment              Palermo   
20          20      sell         house       Villa Giardino   
21          21      sell     apartment              Palermo   
22          22      sell         house    General Rodríguez   
23          23      sell     apartment                Pilar   
24          24      sell     apartment             Castelar   
25          25      sell     apartment             Castelar   
26          26      sell         house   Barrio San Gabriel   
27          27      sell         house  Estancias del Pilar   
28          28      sell     apartment             Castelar   
29          29      sell     apartment               Flores   

                              place_with_parent_names country_name  \
0               |Argentina|Capital Federal|Mataderos|    Argentina   
1         |Argentina|Bs.As. G.B.A. Zona Sur|La Plata|    Argentina   
2               |Argentina|Capital Federal|Mataderos|    Argentina   
3                 |Argentina|Capital Federal|Liniers|    Argentina   
4   |Argentina|Buenos Aires Costa Atlántica|Mar de...    Argentina   
5                 |Argentina|Entre Ríos|Gualeguaychú|    Argentina   
6   |Argentina|Bs.As. G.B.A. Zona Norte|Vicente Ló...    Argentina   
7                |Argentina|Capital Federal|Belgrano|    Argentina   
8                |Argentina|Capital Federal|Belgrano|    Argentina   
9                        |Argentina|Santa Fe|Rosario|    Argentina   
10                        |Argentina|Córdoba|Córdoba|    Argentina   
11    |Argentina|Bs.As. G.B.A. Zona Norte|San Miguel|    Argentina   
12  |Argentina|Bs.As. G.B.A. Zona Norte|San Isidro...    Argentina   
13   |Argentina|Capital Federal|Palermo|Palermo Soho|    Argentina   
14   |Argentina|Capital Federal|Palermo|Palermo Soho|    Argentina   
15  |Argentina|Bs.As. G.B.A. Zona Norte|San Miguel...    Argentina   
16              |Argentina|Capital Federal|Mataderos|    Argentina   
17  |Argentina|Bs.As. G.B.A. Zona Norte|Tigre|Nord...    Argentina   
18         |Argentina|Bs.As. G.B.A. Zona Norte|Tigre|    Argentina   
19                |Argentina|Capital Federal|Palermo|    Argentina   
20                 |Argentina|Córdoba|Villa Giardino|    Argentina   
21                |Argentina|Capital Federal|Palermo|    Argentina   
22  |Argentina|Bs.As. G.B.A. Zona Oeste|General Ro...    Argentina   
23   |Argentina|Bs.As. G.B.A. Zona Norte|Pilar|Pilar|    Argentina   
24  |Argentina|Bs.As. G.B.A. Zona Oeste|Morón|Cast...    Argentina   
25  |Argentina|Bs.As. G.B.A. Zona Oeste|Morón|Cast...    Argentina   
26  |Argentina|Bs.As. G.B.A. Zona Norte|Tigre|Barr...    Argentina   
27  |Argentina|Bs.As. G.B.A. Zona Norte|Pilar|Esta...    Argentina   
28  |Argentina|Bs.As

In [39]:
df['barrio']= df['place_with_parent_names'].str.split('|', expand=True).rename(columns = lambda x: "string"+str(x+1))['string4']